In [2]:
import os
import sys

In [12]:
# !mkdir -p /home/m3hrdadfi/code/data
# %cd /home/m3hrdadfi/code/data
# !wget https://voice-prod-bundler-ee1969a6ce8178826482b88e843c335139bd3fb4.s3.amazonaws.com/cv-corpus-6.1-2020-12-11/fa.tar.gz && tar -xzf fa.tar.gz
# %cd /home/m3hrdadfi/

In [11]:
import os

lang = "fa"
abs_path_to_data = os.path.join(f"/home/m3hrdadfi/data/{lang}", f"cv{lang}", lang)
save_path = "/".join(abs_path_to_data.split('/')[:-2])
print(abs_path_to_data)
print(save_path)
print()
!ls {save_path}
!ls {abs_path_to_data}/*.tsv

/home/m3hrdadfi/data/fa/cvfa/fa
/home/m3hrdadfi/data/fa

cvfa  fa.tar.gz
/home/m3hrdadfi/data/fa/cvfa/fa/dev.tsv
/home/m3hrdadfi/data/fa/cvfa/fa/invalidated.tsv
/home/m3hrdadfi/data/fa/cvfa/fa/other.tsv
/home/m3hrdadfi/data/fa/cvfa/fa/reported.tsv
/home/m3hrdadfi/data/fa/cvfa/fa/test.tsv
/home/m3hrdadfi/data/fa/cvfa/fa/train.tsv
/home/m3hrdadfi/data/fa/cvfa/fa/validated.tsv


In [13]:
import pandas as pd
import numpy as np
from tqdm import tqdm

In [17]:
test_df = pd.read_csv(f"{abs_path_to_data}/test.tsv", sep="\t")

print(f"Step 0: {len(test_df)}")

test_df["path"] = abs_path_to_data + "/clips/" + test_df["path"]
test_df["status"] = test_df["path"].apply(lambda path: True if os.path.exists(path) else None)
test_df = test_df.dropna(subset=["path"])
test_df = test_df.drop("status", 1)
print(f"Step 1: {len(test_df)}")

test_df = test_df.dropna(subset=["sentence"])
print(f"Step 2: {len(test_df)}")

test_df = test_df[["sentence", "path"]]
test_df = test_df.drop_duplicates(subset="path")
print(f"Step 3: {len(test_df)}")

test_df = test_df.reset_index(drop=True)
test_df.head()

Step 0: 5213
Step 1: 5213
Step 2: 5213
Step 3: 5213


sentence  \
0                          از مهمونداری کنار بکشم   
1                             برو از مهرداد بپرس.   
2                           خب ، تو چیكار می كنی؟   
3  مسقط پایتخت عمان در عربی به معنای محل سقوط است   
4                                   آه، نه اصلاُ!   

                                                path  
0  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
1  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
2  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
3  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
4  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...

In [18]:
_train_df = pd.concat([
    pd.read_csv(f"{abs_path_to_data}/train.tsv", sep="\t"),
    pd.read_csv(f"{abs_path_to_data}/dev.tsv", sep="\t"),
])
print(len(_train_df))

train_df = pd.concat([
    pd.read_csv(f"{abs_path_to_data}/train.tsv", sep="\t"),
    pd.read_csv(f"{abs_path_to_data}/dev.tsv", sep="\t"),
    pd.read_csv(f"{abs_path_to_data}/validated.tsv", sep="\t"),
    pd.read_csv(f"{abs_path_to_data}/other.tsv", sep="\t"),
])
print(f"Step 0: {len(train_df)}")

train_df["path"] = abs_path_to_data + "/clips/" + train_df["path"]
train_df["status"] = train_df["path"].apply(lambda path: True if os.path.exists(path) else None)
train_df = train_df.dropna(subset=["path"])
train_df = train_df.drop("status", 1)
print(f"Step 1: {len(train_df)}")

train_df = train_df.dropna(subset=["sentence"])
print(f"Step 2: {len(train_df)}")

train_df = train_df[["sentence", "path"]]
train_df = train_df.drop_duplicates(subset="path")
print(f"Step 3: {len(train_df)}")

train_df = train_df.sample(frac=1)
train_df = train_df.reset_index(drop=True)
train_df.head()

12806
Step 0: 286975
Step 1: 286975
Step 2: 286975
Step 3: 274169


sentence  \
0                       رآس ، اینجا چه خبره ؟   
1  ممکن است آن را تعمیر کنید وقتی منتظر هستم؟   
2                    دلم برای تو تنگ شده است.   
3                   دارم اتاقم را تمیز میکنم.   
4                      هاورد باهاتون صحبت کنم   

                                                path  
0  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
1  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
2  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
3  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
4  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...

In [19]:
from tqdm import tqdm

testset_indices = []

for index, row in tqdm(test_df.iterrows(), total=len(test_df), position=0):
    _id = row["path"]
    finder = train_df[train_df["path"] == _id]
    if len(finder) > 0:
        testset_indices.extend(list(finder.index))

testset_indices = list(set(testset_indices))
print(f"Found #{len(testset_indices)} test data")

100%|██████████| 5213/5213 [02:58<00:00, 29.27it/s]


Found #5213 test data


In [20]:
print(len(train_df))
train_df = train_df.drop(testset_indices)
print(len(train_df))

274169
268956


In [21]:
import pandas as pd

df = pd.concat([train_df, test_df], axis=0)
print(df.info())
df = df.reset_index(drop=True)
print(df.info())
df.head()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 274169 entries, 0 to 5212
Data columns (total 2 columns):
 #   Column    Non-Null Count   Dtype 
---  ------    --------------   ----- 
 0   sentence  274169 non-null  object
 1   path      274169 non-null  object
dtypes: object(2)
memory usage: 6.3+ MB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 274169 entries, 0 to 274168
Data columns (total 2 columns):
 #   Column    Non-Null Count   Dtype 
---  ------    --------------   ----- 
 0   sentence  274169 non-null  object
 1   path      274169 non-null  object
dtypes: object(2)
memory usage: 4.2+ MB
None


sentence  \
0                       رآس ، اینجا چه خبره ؟   
1  ممکن است آن را تعمیر کنید وقتی منتظر هستم؟   
2                    دلم برای تو تنگ شده است.   
3                   دارم اتاقم را تمیز میکنم.   
4                      هاورد باهاتون صحبت کنم   

                                                path  
0  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
1  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
2  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
3  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
4  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...

In [23]:
import torchaudio
import librosa
import IPython.display as ipd
import numpy as np

def load_audio(path):
    speech, sr = torchaudio.load(path)
    speech = speech[0].numpy().squeeze()    
    speech = librosa.resample(np.asarray(speech), sr, 16_000)
    
    print(speech.shape, sr)
    
    ipd.display(ipd.Audio(data=np.asarray(speech), autoplay=True, rate=16000))

In [22]:
# main_vocab = ["ح", "چ", "ج", "ث", "ت", "پ", "ب", "آ", "ا", "ش", "س", "ژ", "ز", "ر", "ذ", "د", "خ", "ق", "ف", "غ", "ع", "ظ", "ط", "ض", "ص", "ی", "ه", "و", "ن", "م", "ل", "گ", "ک"]
# text = " ".join(df["sentence"].values.tolist())
# vocab = list(sorted(set(text)))

# for v in main_vocab:
#     if v not in vocab:
#         print("v", v)

# print(len(main_vocab), len(vocab))
# print(len(vocab), vocab)

In [27]:
import numpy as np


idx = np.random.randint(0, len(df))
# idx = 6140
sample = df.iloc[idx]
ipd.display(sample)

print()
print(sample["sentence"])
print()
load_audio(sample["path"])

train_df.head()

sentence           می توانید لطفاً سفر را برای من ترتیب دهید؟
path        /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...
Name: 95177, dtype: object


می توانید لطفاً سفر را برای من ترتیب دهید؟

(70272,) 48000


sentence  \
0                       رآس ، اینجا چه خبره ؟   
1  ممکن است آن را تعمیر کنید وقتی منتظر هستم؟   
2                    دلم برای تو تنگ شده است.   
3                   دارم اتاقم را تمیز میکنم.   
4                      هاورد باهاتون صحبت کنم   

                                                path  
0  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
1  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
2  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
3  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
4  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...

In [29]:
new_train_df = train_df.copy()
new_train_df["_path"] = new_train_df["path"]
new_train_df["path"] = new_train_df["path"].apply(lambda t: os.path.join("/home/m3hrdadfi/data/fa/clips", t.split("/")[-1]))
print(new_train_df.info())
print(new_train_df.iloc[0]["_path"])
print(new_train_df.iloc[0]["path"])
new_train_df.head()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 268956 entries, 0 to 274168
Data columns (total 3 columns):
 #   Column    Non-Null Count   Dtype 
---  ------    --------------   ----- 
 0   sentence  268956 non-null  object
 1   path      268956 non-null  object
 2   _path     268956 non-null  object
dtypes: object(3)
memory usage: 8.2+ MB
None
/home/m3hrdadfi/data/fa/cvfa/fa/clips/common_voice_fa_20100079.mp3
/home/m3hrdadfi/data/fa/clips/common_voice_fa_20100079.mp3


sentence  \
0                       رآس ، اینجا چه خبره ؟   
1  ممکن است آن را تعمیر کنید وقتی منتظر هستم؟   
2                    دلم برای تو تنگ شده است.   
3                   دارم اتاقم را تمیز میکنم.   
4                      هاورد باهاتون صحبت کنم   

                                                path  \
0  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
1  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
2  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
3  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
4  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   

                                               _path  
0  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
1  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
2  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
3  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
4  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...

In [30]:
new_test_df = test_df.copy()
new_test_df["_path"] = new_test_df["path"]
new_test_df["path"] = new_test_df["path"].apply(lambda t: os.path.join("/home/m3hrdadfi/data/fa/clips", t.split("/")[-1]))
print(new_test_df.info())
print(new_test_df.iloc[0]["_path"])
print(new_test_df.iloc[0]["path"])
new_test_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5213 entries, 0 to 5212
Data columns (total 3 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   sentence  5213 non-null   object
 1   path      5213 non-null   object
 2   _path     5213 non-null   object
dtypes: object(3)
memory usage: 122.3+ KB
None
/home/m3hrdadfi/data/fa/cvfa/fa/clips/common_voice_fa_18325365.mp3
/home/m3hrdadfi/data/fa/clips/common_voice_fa_18325365.mp3


sentence  \
0                          از مهمونداری کنار بکشم   
1                             برو از مهرداد بپرس.   
2                           خب ، تو چیكار می كنی؟   
3  مسقط پایتخت عمان در عربی به معنای محل سقوط است   
4                                   آه، نه اصلاُ!   

                                                path  \
0  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
1  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
2  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
3  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
4  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   

                                               _path  
0  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
1  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
2  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
3  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
4  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...

In [31]:
import shutil
from tqdm import tqdm

In [32]:
print(save_path)

/home/m3hrdadfi/data/fa


In [33]:
!mkdir -p {save_path}/clips
!mkdir -p {save_path}/augs

In [34]:
for index, row in tqdm(new_train_df.iterrows(), position=0, total=len(new_train_df)):
    shutil.copy(row["_path"], row["path"])

100%|██████████| 268956/268956 [02:40<00:00, 1675.19it/s]


In [35]:
for index, row in tqdm(new_test_df.iterrows(), position=0, total=len(new_test_df)):
    shutil.copy(row["_path"], row["path"])

100%|██████████| 5213/5213 [00:01<00:00, 4777.79it/s]


In [36]:
# aug_train_df = new_train_df.copy()
aug_train_df = new_train_df.sample(frac=0.1)
aug_train_df = aug_train_df.reset_index(drop=True)
aug_train_df["_path"] = aug_train_df["path"]
aug_train_df["path"] = aug_train_df["path"].apply(lambda t: "/".join(t.split('.')[:-1]).replace("clips", "augs") + "_aug.mp3.wav")
print(aug_train_df.info())
aug_train_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 26896 entries, 0 to 26895
Data columns (total 3 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   sentence  26896 non-null  object
 1   path      26896 non-null  object
 2   _path     26896 non-null  object
dtypes: object(3)
memory usage: 630.5+ KB
None


sentence  \
0                               کدامیک ارزان تر است؟   
1                آیا قرمز را بیشتر از آبی دوست داری؟   
2                                 من می خوام کمک کنم   
3  در آفریقای جنوبی، برنامهای به نام دختران تکنو هست   
4  حالا، این موضوع به ما فرصت ایجاد چند سناریو را...   

                                                path  \
0  /home/m3hrdadfi/data/fa/augs/common_voice_fa_2...   
1  /home/m3hrdadfi/data/fa/augs/common_voice_fa_2...   
2  /home/m3hrdadfi/data/fa/augs/common_voice_fa_1...   
3  /home/m3hrdadfi/data/fa/augs/common_voice_fa_1...   
4  /home/m3hrdadfi/data/fa/augs/common_voice_fa_1...   

                                               _path  
0  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...  
1  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...  
2  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...  
3  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...  
4  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...

In [37]:
print(aug_train_df.iloc[0]["_path"])
print(aug_train_df.iloc[0]["path"])

/home/m3hrdadfi/data/fa/clips/common_voice_fa_20109281.mp3
/home/m3hrdadfi/data/fa/augs/common_voice_fa_20109281_aug.mp3.wav


In [38]:
# augmentation

from audiomentations import Compose, AddGaussianNoise, TimeStretch, PitchShift, Shift, Gain
import numpy as np
import soundfile as sf

augment = Compose([
#     AddGaussianNoise(min_amplitude=0.001, max_amplitude=0.015, p=0.5),
#     PitchShift(min_semitones=-1, max_semitones=2, p=0.2),
#     Gain(min_gain_in_db=-6, max_gain_in_db=6, p=0.8)
    AddGaussianNoise(min_amplitude=0.001, max_amplitude=0.015, p=0.5),
    TimeStretch(min_rate=0.8, max_rate=1.25, p=0.5),
    PitchShift(min_semitones=-4, max_semitones=4, p=0.5),
])

def augmented_speech_file_to_array_fn(in_path, out_path):
    speech_array, sampling_rate = torchaudio.load(in_path)
    speech_array = speech_array.squeeze().numpy()
    speech_array = augment(samples=speech_array, sample_rate=sampling_rate)
    sf.write(out_path, speech_array, sampling_rate, "PCM_24")

In [40]:
for index, row in tqdm(aug_train_df.iterrows(), position=0, total=len(aug_train_df)):
    augmented_speech_file_to_array_fn(row["_path"], row["path"])
# !ls

100%|██████████| 26896/26896 [1:18:09<00:00,  5.74it/s]


In [42]:
new_train_aug_df = pd.concat([new_train_df, aug_train_df], axis=0)
# new_train_aug_df = new_train_df.copy()
new_train_aug_df = new_train_aug_df.sample(frac=1)
new_train_aug_df = new_train_aug_df.reset_index(drop=True)
print(new_train_aug_df.info())
new_train_aug_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 295852 entries, 0 to 295851
Data columns (total 3 columns):
 #   Column    Non-Null Count   Dtype 
---  ------    --------------   ----- 
 0   sentence  295852 non-null  object
 1   path      295852 non-null  object
 2   _path     295852 non-null  object
dtypes: object(3)
memory usage: 6.8+ MB
None


sentence  \
0  اما دیدم نه،هیچ جوره نمیتونم ببخشمش به خدا گفت...   
1                                        برای امروز.   
2  چون اگر میدانیم چیزی که بیگناه در نظر میگیریم ...   
3              ضمیر من را بدانید -- آقا، خانم، ایشان   
4                           تا تقویت و تکثیرشان کنیم   

                                                path  \
0  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
1  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
2  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
3  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
4  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   

                                               _path  
0  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
1  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
2  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
3  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
4  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...

In [43]:
save_path

'/home/m3hrdadfi/data/fa'

In [44]:
new_train_df.to_csv(f"{save_path}/train_no_aug.csv", sep="\t", encoding="utf-8", index=False)
new_train_aug_df.to_csv(f"{save_path}/train_with_aug.csv", sep="\t", encoding="utf-8", index=False)
new_test_df.to_csv(f"{save_path}/test.csv", sep="\t", encoding="utf-8", index=False)

In [45]:
new_train_df.count()

sentence    268956
path        268956
_path       268956
dtype: int64

In [46]:
new_test_df.count()

sentence    5213
path        5213
_path       5213
dtype: int64

In [47]:
import pandas as pd

import os
from tqdm import tqdm

In [48]:
train_df = pd.read_csv(f"{save_path}/train_no_aug.csv", sep="\t")
print(train_df.info())
train_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 268956 entries, 0 to 268955
Data columns (total 3 columns):
 #   Column    Non-Null Count   Dtype 
---  ------    --------------   ----- 
 0   sentence  268956 non-null  object
 1   path      268956 non-null  object
 2   _path     268956 non-null  object
dtypes: object(3)
memory usage: 6.2+ MB
None


sentence  \
0                       رآس ، اینجا چه خبره ؟   
1  ممکن است آن را تعمیر کنید وقتی منتظر هستم؟   
2                    دلم برای تو تنگ شده است.   
3                   دارم اتاقم را تمیز میکنم.   
4                      هاورد باهاتون صحبت کنم   

                                                path  \
0  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
1  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
2  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
3  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
4  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   

                                               _path  
0  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
1  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
2  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
3  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
4  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...

In [49]:
test_df = pd.read_csv(f"{save_path}/test.csv", sep="\t")
print(test_df.info())
test_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5213 entries, 0 to 5212
Data columns (total 3 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   sentence  5213 non-null   object
 1   path      5213 non-null   object
 2   _path     5213 non-null   object
dtypes: object(3)
memory usage: 122.3+ KB
None


sentence  \
0                          از مهمونداری کنار بکشم   
1                             برو از مهرداد بپرس.   
2                           خب ، تو چیكار می كنی؟   
3  مسقط پایتخت عمان در عربی به معنای محل سقوط است   
4                                   آه، نه اصلاُ!   

                                                path  \
0  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
1  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
2  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
3  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   
4  /home/m3hrdadfi/data/fa/clips/common_voice_fa_...   

                                               _path  
0  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
1  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
2  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
3  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...  
4  /home/m3hrdadfi/data/fa/cvfa/fa/clips/common_v...

In [50]:
non_existed_train = []

for index, row in tqdm(train_df.iterrows(), total=len(train_df), position=0):
    if not os.path.exists(row["path"]):
        non_existed_train.extends(list(index))
        break

100%|██████████| 268956/268956 [00:11<00:00, 24344.12it/s]


In [51]:
non_existed_train

[]

In [42]:
# import numpy as np


# idx = np.random.randint(0, len(train_df))
# # idx = 6140
# sample = train_df.iloc[idx]
# ipd.display(sample)
# # print(sample.iloc[idx]["prev_sentence"])
# print()
# print(sample["prev_sentence"])
# print(sample["sentence"])
# print()
# load_audio(sample["path"])

In [43]:
# train_df_half = train_df.copy()
# print(train_df_half.shape)
# train_df_half = train_df_half.dropna()
# print(train_df_half.shape)
# train_df_half = train_df_half.drop_duplicates()
# print(train_df_half.shape)

# train_df_half = train_df_half.sample(frac=0.5)
# train_df_half = train_df_half.reset_index(drop=True)
# print(train_df_half.shape)

In [44]:
# train_df_half.to_csv(f"{save_path}/train_no_aug_half.csv", sep="\t", encoding="utf-8", index=False)